In [1]:
from glob import glob
from os.path import join
import pandas as pd

from maps.pings import Pings
from maps.maps import FoliumMap

location_data_dirpath = '../../data/locations/'
photo_metadata_dirpath = '../../data/photo_metadata'

pings_data_path = join(location_data_dirpath, 'pings.hdf')
posts_path = join(photo_metadata_dirpath, 'posts.hdf')

%reload_ext autoreload
%autoreload 2

In [2]:
# load geolocated photos
max_dt_ping = 3600/4 # 15 minutes
posts = pd.read_hdf(posts_path, 'data')
no_gps_data = (~posts.geotagged & (posts.dt_ping >= max_dt_ping))
posts.loc[no_gps_data, ['latitude', 'longitude']] = float('nan')
photos = posts[~posts.latitude.isna()]

/Users/Sebi/.virtualenvs/web/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2858: PerformanceWarning: indexing past lexsort depth may impact performance.
  raw_cell, store_history, silent, shell_futures)


In [4]:
# # load all pings
# ping_data = pd.read_hdf(pings_data_path, 'data')
# ping_data = ping_data[ping_data.accuracy < 3000]
# ping_data = ping_data[ping_data.altitude < 4000]

# # geocode trip pings
# pings = Pings(ping_data.loc['2019-07-24':], 2)
# pings.cluster(use_weights=False, n_clusters=500)
# pings.build_geocodes()
# pings.geocode()

# save clustered pings
# with open(pickled_pings_path, 'wb') as file:
#     pickle.dump(pings, file)

import pickle

# load clustered pings
pickled_pings_path = join(location_data_dirpath, 'clustered_pings.pkl')
with open(pickled_pings_path, 'rb') as file:
    pings = pickle.load(file)

In [5]:
# label time periods
time_periods = {
    'July': ('2019-07-24', '2019-07-28'),
    'August-November': ('2019-08-11', '2019-11-09'),
    'December': ('2019-12-01', '2019-12-24'),
    'February': ('2020-02-25', '2020-03-17')
}

pings.label_timespans('time_period', time_periods)

In [6]:
trip_ids = {'Highway 1': ('2019-07-24 03:31:58', '2019-07-31 23:24:51'),
 'France': ('2019-08-11 20:50:39', '2019-08-21 11:47:50'),
 'Italian Coast': ('2019-08-20 08:01:17', '2019-09-11 06:55:10'),
 'England': ('2019-09-11 00:04:16', '2019-09-25 07:33:45'),
 'Central Europe': ('2019-09-25 03:08:30', '2019-10-22 05:09:37'),
 'Catalonia': ('2019-11-02 04:49:07', '2019-11-07 06:22:22'),
 'Morocco': ('2019-12-03 12:36:19', '2019-12-12 18:15:52'),
 'Italian Alps': ('2019-12-13 02:43:52', '2019-12-23 19:23:37'),
 'Rocky Mountains': ('2020-02-25 01:14:48', '2020-03-17 22:27:32')}

pings.label_timespans('trip_id', trip_ids)

In [213]:
# highway1_drive = [d for d in drives if 'San Diego' in d.cities][0]
# france_flights = [f for f in flights if 'FR' in f.countries and f.stop_ts<'2019-11-01']
# italian_coast_flights = [f for f in flights if 'IT' in f.countries and f.stop_ts<'2019-11-01']
# england_flights = [f for f in flights if 'GB' in f.countries and f.stop_ts < '2019-09-26']
# central_europe_flights = [f for f in flights if 'CZ' in f.countries]
# catalonia_flights = [f for f in flights if 'ES' in f.countries and f.stop_ts<'2019-12-01']
# morocco_flights = [f for f in flights if 'MA' in f.countries]
# italian_alps_flights = [f for f in flights if 'IT' in f.countries and f.start_ts>'2019-12-01']
# rockies_drive = [d for d in drives if 'Wyoming' in d.states][0]

# # label trips
# trip_ids = {
#     'Highway 1': (highway1_drive.start_ts, highway1_drive.stop_ts),
#     'France': (france_flights[0].start_ts, france_flights[-1].stop_ts),
#     'Italian Coast': (italian_coast_flights[0].start_ts, italian_coast_flights[-1].stop_ts),
#     'England': (england_flights[0].start_ts, england_flights[-1].stop_ts),
#     'Central Europe': (central_europe_flights[0].start_ts, central_europe_flights[-1].stop_ts),
#     'Catalonia': (catalonia_flights[0].start_ts, catalonia_flights[-1].stop_ts),
#     'Morocco': (morocco_flights[0].start_ts, morocco_flights[-1].stop_ts),
#     'Italian Alps': (italian_alps_flights[0].start_ts, italian_alps_flights[-1].stop_ts),
#     'Rocky Mountains': (rockies_drive.start_ts, rockies_drive.stop_ts)}

# Composite map

In [108]:
from maps.segments import find_drives, find_flights
from maps.trips import Trip


class TripGenerator:
    
    def __init__(self, pings, photos):
        
        self.pings = pings
        self.photos = photos
        
        # find trains/planes/drives
        rail = [
            TrainSegment(pings.pings.loc['SMB'].loc['2019-08-15 22:31:30':'2019-08-16 07:23:57']),
            TrainSegment(pings.pings.loc['CMB'].loc['2019-09-02 04:43:04':'2019-09-02 06:03:54'])]
        air = find_flights(pings.pings.loc['SMB'])
        land = find_drives(pings, rail+air)
        
        self.segments = {
            'air': air,
            'rail': rail,
            'land': land}
        
    def get_trip_segments(self, *trip_ids):
        trip_segments = {'air': [], 'rail': [], 'land': []} 
        for trip_id in trip_ids:
            for segment_type, segments in self.segments.items():
                _ = [trip_segments[segment_type].append(x) for x in segments if trip_id in x.trip_ids]
        return trip_segments
    
    def get_trip_pings(self, *trip_ids):
        match = lambda x: len(set(trip_ids).intersection(set(x))) > 0
        trip_pings = self.pings.flattened[self.pings.flattened.trip_id.apply(match)]
        return trip_pings
    
    def get_trip_photos(self, trip_pings):
        t0, t1 = trip_pings.index.min(), trip_pings.index.max()
        trip_photos = self.photos[self.photos.timestamp.between(t0, t1)]
        return trip_photos
    
    def get_trip(self, *trip_ids):
        segments = self.get_trip_segments(*trip_ids)
        pings = self.get_trip_pings(*trip_ids)
        photos = self.get_trip_photos(pings)
        return Trip(segments, pings, photos)

In [132]:
# compile trip generator
trips = TripGenerator(pings, photos)

# Generate trip

In [569]:
trip_names = ['Highway 1',
'France',
'Italian Coast',
'England',
'Central Europe',
'Catalonia',
'Morocco',
'Italian Alps',
'Rocky Mountains']

In [667]:
trip_name = 'Rocky Mountains'
filename = '-'.join([x.lower() for x in trip_name.split()]) +'.html'

In [672]:
trip_ids = (trip_name,)
trip = trips.get_trip(*trip_ids)
trip.build_map(zoom_start=5)
trip.add_travel_to_map(weight=6, drive_color='black')
trip.add_photos_to_map(True, maxClusterRadius=50)
trip.add_heatmap_to_map()
#trip.add_video_to_map()
trip.add_layer_control()

In [673]:
trip.map

In [674]:
trip.save_map('../travel/maps/{:s}'.format(filename))

In [683]:
trips.photos.loc[('Austria', 'IMG_1942.jpg', 'PowerShot G9 X Mark II')]

path                /Volumes/bernasek_t5/photos/lightroom/rendered...
timestamp                                         2019-10-05 11:01:54
time_shot_pst                                     2019:10:05 11:01:54
time_shot_local                                   2019:10:05 11:01:54
time_rendered                                     2020:04:09 17:04:54
geotagged                                                       False
latitude_native                                                   NaN
longitude_native                                                  NaN
latitude_ping                                                 47.3612
longitude_ping                                                13.2005
accuracy                                                           10
owner                                                             CMB
time_ping                                         2019-10-05 11:02:39
dt_ping                                                            45
latitude            

In [ ]:
"""
lines tooltip --> driving/train/ flight to X
marker tooltip --> flighjt to X on X date
harburg and dinklesbuhl getting mixed up
augustiner coaster is wrong

figure out page structure
"""

In [15]:
m = FoliumMap()
m.build_map(width='100%', height='100%', zoom_start=3)

layers = {name: FeatureGroup(name=name, show=False).add_to(m.map) for name in trip_ids.keys()}
fg_heatmap = FeatureGroup(name='Heatmap', show=False).add_to(m.map)
fg_photos = FeatureGroup(name='Photos', show=True).add_to(m.map)

for flight in flights:
    obj = flight.get_line(color='black', weight=3, opacity=0.2)
    obj.add_to(layers[flight.layer_id])
    
for train in trains:
    obj = train.get_line(color='blue', weight=3, opacity=0.2)
    obj.add_to(layers[train.layer_id])
    
for drive in drives:
    hm = drive.get_heatmap()
    hm.add_to(fg_heatmap)
    
    if drive.layer_id is not None:
        obj = drive.get_antpath(color='red', weight=3)
        obj.add_to(layers[drive.layer_id])
    
# photo clusters
mc = MarkerCluster(
    maxClusterRadius=20,
    showCoverageOnHover=False,
    zoomToBoundsOnClick=True,
    spiderfyOnMaxZoom=True).add_to(fg_photos)

for idx, photo in photos.iterrows():
    xy = photo[Pings.GPS_INDEX].values.astype(float)
    popup = ImagePopup(photo.imgur_id, photo.caption).popup
    tooltip = photo.caption
    Marker(xy, popup=popup, 
           tooltip=tooltip, 
           icon=Icon('darkred', icon_color='white', icon='image', prefix='fa')
          ).add_to(mc)
        
# add the layer control
LayerControl().add_to(m.map)

m.map